# The Battle of Neighborhoods
Determining the best neighborhood in Miami for restaurateur Matilda to open her first west coast establishment.

## Introduction
Matilda is a restaurateur from New York City, who has established two successful Italian restaurants on the east coast. She plans on expanding her restaurant business to Miami and would like to open an Italian restaurant in a neighborhood with an existing clientele for such cuisine. With that in mind, I will be helping Matilda in determining the best neighborhood to open up her new restaurant in Miami using data from the Foursquare API.

## Problem Statement
The objective of this project is to determine the best Miami neighborhood for Matilda to establish her new Italian restaurant. However, she does not have any knowledge on where Italian restaurants are currently located in Miami, consequently, where there may also be an existing clientele for her restaurant. Using machine learning and data from the Foursquare API, I will be able to answer the question of: **_which neighborhoods should a restaurateur open an Italian restaurant in Miami?_**

## Target Audience
The target audience for this solution is a restaurateur who seeks to open an Italian restaurant in Miami but does not have the knowledge to know where they should do so.

## Data
The data required to complete this project would consist of:
- Neighborhoods in Miami
- Latitude and Longitude of Neighborhoods in Miami
- Italian Restaurant Venues in Miami

To obtain this data, I will:
1. Scrape websites for all neighborhoods in Miami
2. Obtain latitude and longitude of those neighborhoods
3. Use the Foursquare API to retrieve Italian restaurant venues in Miami neighborhoods


## 1. Import all necessary packages and modules.

In [6]:
# Start by importing all relevant libraries.
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim

import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


## 2. Scrape Wikipedia for all neighborhoods in Los Angeles.

In [7]:
! pip install beautifulsoup4
! pip install lxml
! pip install html5lib

In [74]:
# Using BeautifulSoup to call out the contents of the webpage.
from bs4 import BeautifulSoup
url = 'https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Miami'
page = requests.get(url)
soup = BeautifulSoup(page.content, 'lxml')
soup

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of neighborhoods in Miami - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"c3b389e1-6135-4d77-bcd8-a2dfcf605e5a","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_neighborhoods_in_Miami","wgTitle":"List of neighborhoods in Miami","wgCurRevisionId":986332524,"wgRevisionId":986332524,"wgArticleId":7122027,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Neighborhoods in Miami","Lists of neighborhoods in U.S. cities","Miami-related lists"],"wgPageContentLanguage":"en","w

## 3. Extract neighborhood names from HTML and transform into a DataFrame.

In [75]:
# Extracting results from the table specifically.
results = soup.find(class_='wikitable sortable')
results

<table class="wikitable sortable">
<caption>Neighborhoods in Miami<sup class="reference" id="cite_ref-2"><a href="#cite_note-2">[2]</a></sup>
</caption>
<tbody><tr bgcolor="#CCCCCC">
<th>Neighborhood</th>
<th><a href="/wiki/Demonym" title="Demonym">Demonym</a></th>
<th>Population<br/>2010</th>
<th>Population/<br/>Km²</th>
<th class="unsortable">Sub-neighborhoods</th>
<th>Coordinates
</th></tr>
<tr>
<td><a href="/wiki/Allapattah" title="Allapattah">Allapattah</a></td>
<td align="right"></td>
<td align="right">54,289</td>
<td align="right">4,401</td>
<td></td>
<td>25.815,-80.224
</td></tr>
<tr>
<td><a href="/wiki/Arts_%26_Entertainment_District" title="Arts &amp; Entertainment District">Arts &amp; Entertainment District</a></td>
<td align="right"></td>
<td align="right">11,033</td>
<td align="right">7,948</td>
<td></td>
<td>25.799,-80.190
</td></tr>
<tr>
<td><a href="/wiki/Brickell" title="Brickell">Brickell</a></td>
<td align="right"><i>Brickellite</i></td>
<td align="right">31,759</td>

In [76]:
# Reading the table into a dataframe.
data_frame = pd.read_html(str(results))[0]
data_frame

Neighborhood          Demonym            Population2010  \
0                      Allapattah              NaN                     54289   
1   Arts & Entertainment District              NaN                     11033   
2                        Brickell      Brickellite                     31759   
3                     Buena Vista              NaN                      9058   
4                   Coconut Grove          Grovite                     20076   
5                       Coral Way              NaN                     35062   
6                 Design District              NaN                      3573   
7                        Downtown       Downtowner  71,000 (13,635 CBD only)   
8                       Edgewater              NaN                     15005   
9                         Flagami              NaN                     50834   
10              Grapeland Heights              NaN                     14004   
11                Health District              NaN                      2705   
12                   Liberty City              NaN                     19725   
13                   Little Haiti              NaN                     29760   
14                  Little Havana              NaN                     76163   
15                    Lummus Park              NaN                      3027   
16                        Midtown        Midtowner                         -   
17                       Overtown           Towner                      6736   
18                      Park West              NaN                      4655   
19                      The Roads              NaN                      7327   
20                 Upper Eastside  Upper Eastsider                     12525   
21               Venetian Islands              NaN                       NaN   
22                   Virginia Key              NaN                        14   
23                   West Flagler              NaN                     31407   
24                        Wynwood       Wynwoodian                      7277   
25                          Miami          Miamian                    399457   

   Population/Km²                                  Sub-neighborhoods  \
0            4401                                                NaN   
1            7948                                                NaN   
2           14541                                      West Brickell   
3            3540  Buena Vista East Historic District and Design ...   
4            3091  Center Grove, Northeast Coconut Grove, Southwe...   
5            4496  Coral Gate, Golden Pines, Shenandoah, Historic...   
6            3623                                                NaN   
7           10613  Brickell, Central Business District (CBD), Dow...   
8            6675                                                NaN   
9            5665           Alameda, Grapeland Heights, and Fairlawn   
10           4130                                                NaN   
11           2148                                                NaN   
12           3733                                                NaN   
13           3840                      Lemon City (aka Little River)   
14           8423  Riverside and South River Drive Historic District   
15           3680                                                NaN   
16              -                              Edgewater and Wynwood   
17           3405                                      Spring Garden   
18           3635                                                NaN   
19           4899                                                NaN   
20           2513  Bay Point Estates, Bayside District, Belle Mea...   
21            NaN               Biscayne Island and San Marco Island   
22              -                                                NaN   
23           4428                                                NaN   
24           2983  Wynwood Art District and Wynwood Fashion 

In [77]:
# Only taking the relevant data of neighborhood names and coordinates.
miamiNeighborhoods = data_frame[['Neighborhood', 'Coordinates']]
miamiNeighborhoods

Neighborhood    Coordinates
0                      Allapattah  25.815-80.224
1   Arts & Entertainment District  25.799-80.190
2                        Brickell  25.758-80.193
3                     Buena Vista  25.813-80.192
4                   Coconut Grove  25.712-80.257
5                       Coral Way  25.750-80.283
6                 Design District  25.813-80.193
7                        Downtown  25.774-80.193
8                       Edgewater  25.802-80.190
9                         Flagami  25.762-80.316
10              Grapeland Heights  25.792-80.258
11                Health District            NaN
12                   Liberty City  25.832-80.225
13                   Little Haiti  25.824-80.191
14                  Little Havana  25.773-80.215
15                    Lummus Park  25.777-80.201
16                        Midtown  25.807-80.193
17                       Overtown  25.787-80.201
18                      Park West  25.785-80.193
19                      The Roads  25.756-80.207
20                 Upper Eastside  25.830-80.183
21               Venetian Islands  25.791-80.161
22                   Virginia Key  25.736-80.155
23                   West Flagler  25.775-80.243
24                        Wynwood  25.804-80.199
25                          Miami            NaN

In [78]:
# Dropping NaN values from the coordinates column.
miamiNeighborhoods = miamiNeighborhoods.dropna()
miamiNeighborhoods

Neighborhood    Coordinates
0                      Allapattah  25.815-80.224
1   Arts & Entertainment District  25.799-80.190
2                        Brickell  25.758-80.193
3                     Buena Vista  25.813-80.192
4                   Coconut Grove  25.712-80.257
5                       Coral Way  25.750-80.283
6                 Design District  25.813-80.193
7                        Downtown  25.774-80.193
8                       Edgewater  25.802-80.190
9                         Flagami  25.762-80.316
10              Grapeland Heights  25.792-80.258
12                   Liberty City  25.832-80.225
13                   Little Haiti  25.824-80.191
14                  Little Havana  25.773-80.215
15                    Lummus Park  25.777-80.201
16                        Midtown  25.807-80.193
17                       Overtown  25.787-80.201
18                      Park West  25.785-80.193
19                      The Roads  25.756-80.207
20                 Upper Eastside  25.830-80.183
21               Venetian Islands  25.791-80.161
22                   Virginia Key  25.736-80.155
23                   West Flagler  25.775-80.243
24                        Wynwood  25.804-80.199

In [79]:
# Split up latitude and longitude values for each neighborhood because they had been in a single column.
new = miamiNeighborhoods['Coordinates'].str.split("-", n=1, expand=True)
miamiNeighborhoods['Latitude'] = new[0]
miamiNeighborhoods['Longitude'] = new[1]
miamiNeighborhoods['Longitude'] = '-' + miamiNeighborhoods['Longitude'].astype(str)
miamiNeighborhoods.drop(columns=['Coordinates'], inplace=True)
miamiNeighborhoods

<ipython-input-79-94e30b2fb90c>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  miamiNeighborhoods['Latitude'] = new[0]
<ipython-input-79-94e30b2fb90c>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  miamiNeighborhoods['Longitude'] = new[1]
<ipython-input-79-94e30b2fb90c>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/us

Neighborhood Latitude Longitude
0                      Allapattah   25.815   -80.224
1   Arts & Entertainment District   25.799   -80.190
2                        Brickell   25.758   -80.193
3                     Buena Vista   25.813   -80.192
4                   Coconut Grove   25.712   -80.257
5                       Coral Way   25.750   -80.283
6                 Design District   25.813   -80.193
7                        Downtown   25.774   -80.193
8                       Edgewater   25.802   -80.190
9                         Flagami   25.762   -80.316
10              Grapeland Heights   25.792   -80.258
12                   Liberty City   25.832   -80.225
13                   Little Haiti   25.824   -80.191
14                  Little Havana   25.773   -80.215
15                    Lummus Park   25.777   -80.201
16                        Midtown   25.807   -80.193
17                       Overtown   25.787   -80.201
18                      Park West   25.785   -80.193
19                      The Roads   25.756   -80.207
20                 Upper Eastside   25.830   -80.183
21               Venetian Islands   25.791   -80.161
22                   Virginia Key   25.736   -80.155
23                   West Flagler   25.775   -80.243
24                        Wynwood   25.804   -80.199

## 4. Map out Miami and its neighborhoods for exploration.
Creating a map of Miami and its neighborhoods for exploration using Folium.

In [80]:
address = 'Miami, Florida'

geolocator = Nominatim(user_agent = 'miami_explorer')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinate of miami are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of miami are 25.7742658, -80.1936589.


In [81]:
# Turn latitude and longitude values into float values instead of string.
miamiNeighborhoods['Latitude'] = miamiNeighborhoods['Latitude'].astype(float)
miamiNeighborhoods['Longitude'] = miamiNeighborhoods['Longitude'].astype(float)

<ipython-input-81-58c984669ff4>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  miamiNeighborhoods['Latitude'] = miamiNeighborhoods['Latitude'].astype(float)
<ipython-input-81-58c984669ff4>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  miamiNeighborhoods['Longitude'] = miamiNeighborhoods['Longitude'].astype(float)


In [82]:
# Map out Miami and its boroughs and neighborhoods.
map_miami = folium.Map(location=[latitude,longitude], zoom_start=10)

for lat, lng, neighborhood in zip(miamiNeighborhoods['Latitude'], miamiNeighborhoods['Longitude'], miamiNeighborhoods['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_miami)

map_miami

## 5. Extracting top venues for each of the neighborhoods.
Using the FourSquare API to extract top venues for each of the neighborhoods.

In [83]:
# Define Foursquare API credentials
CLIENT_ID = 'L05WHQYTATFIFXCRVROYESBS0YG53P55L5NX1XMOY2JC30M1' # your Foursquare ID
CLIENT_SECRET = 'VNMSQBDIJ2EYNM4BQ5BXOFJMGVZ5ATKHKKQYJY2SLV2VR3U0' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: L05WHQYTATFIFXCRVROYESBS0YG53P55L5NX1XMOY2JC30M1
CLIENT_SECRET:VNMSQBDIJ2EYNM4BQ5BXOFJMGVZ5ATKHKKQYJY2SLV2VR3U0


In [84]:
# Define a function to obtain top venues for each postal code.
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [85]:
# Use function to get top venues for each of the postal codes.
miami_venues = getNearbyVenues(names=miamiNeighborhoods['Neighborhood'], latitudes=miamiNeighborhoods['Latitude'], longitudes=miamiNeighborhoods['Longitude'])

Allapattah
Arts & Entertainment District
Brickell
Buena Vista
Coconut Grove
Coral Way
Design District
Downtown
Edgewater
Flagami
Grapeland Heights
Liberty City
Little Haiti
Little Havana
Lummus Park
Midtown
Overtown
Park West
The Roads
Upper Eastside
Venetian Islands
Virginia Key
West Flagler
Wynwood


In [86]:
miami_venues.head()

Neighborhood  Neighborhood Latitude  \
0                     Allapattah                 25.815   
1                     Allapattah                 25.815   
2  Arts & Entertainment District                 25.799   
3  Arts & Entertainment District                 25.799   
4  Arts & Entertainment District                 25.799   

   Neighborhood Longitude                           Venue  Venue Latitude  \
0                 -80.224   Three Fingers Liquor & Lounge       25.815408   
1                 -80.224                            Ross       25.815820   
2                 -80.190                    Bunnie Cakes       25.799544   
3                 -80.190            Yodi's Threading Spa       25.800490   
4                 -80.190  TRIO - Mind Body Spirit Studio       25.799573   

   Venue Longitude    Venue Category  
0       -80.224361            Lounge  
1       -80.221753  Department Store  
2       -80.190953      Cupcake Shop  
3       -80.189093               Spa  
4       -80.190972       Yoga Studio

In [87]:
miami_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                   
Allapattah                                         2                       2   
Arts & Entertainment District                     20                      20   
Brickell                                          53                      53   
Buena Vista                                       29                      29   
Coconut Grove                                      3                       3   
Coral Way                                          9                       9   
Design District                                   28                      28   
Downtown                                          50                      50   
Edgewater                                         44                      44   
Flagami                                            9                       9   
Grapeland Heights                                  7                       7   
Liberty City                                       3                       3   
Little Haiti                                      24                      24   
Little Havana                                      8                       8   
Lummus Park                                       12                      12   
Midtown                                           43                      43   
Overtown                                           3                       3   
Park West                                         26                      26   
The Roads                                          9                       9   
Upper Eastside                                     6                       6   
Venetian Islands                                   3                       3   
Virginia Key                                       1                       1   
West Flagler                                       8                       8   
Wynwood                                           76                      76   

                               Venue  Venue Latitude  Venue Longitude  \
Neighborhood                                                            
Allapattah                         2               2                2   
Arts & Entertainment District     20              20               20   
Brickell                          53              53               53   
Buena Vista                       29              29               29   
Coconut Grove                      3               3                3   
Coral Way                          9               9                9   
Design District                   28              28               28   
Downtown                          50              50               50   
Edgewater                         44              44               44   
Flagami                            9               9                9   
Grapeland Heights                  7               7                7   
Liberty City                       3               3                3   
Little Haiti                      24              24               24   
Little Havana                      8               8                8   
Lummus Park                       12              12               12   
Midtown                           43              43               43   
Overtown                           3               3                3   
Park West                         26              26               26   
The Roads                          9               9                9   
Upper Eastside                     6               6                6   
Venetian Islands                   3               3                3   
Virginia Key                       1               1                1   
West Flagler                       8               8                8   
Wynwood                           76              76               76   

                               Venue Category  
Nei

In [88]:
print('There are {} uniques categories.'.format(len(miami_venues['Venue Category'].unique())))

There are 137 uniques categories.


In [89]:
# Checking to see if Italian Restaurant is a venue category in our results.
'Italian Restaurant' in miami_venues['Venue Category'].unique()

True

In [97]:
# Analyzing individual neighborhoods.

# Creating dummy values for one-hot encoding.
miami_onehot = pd.get_dummies(miami_venues[['Venue Category']], prefix="", prefix_sep="")
miami_onehot.drop(columns=['Neighborhood'], inplace=True)
miami_onehot

American Restaurant  Aquarium  Arcade  Arepa Restaurant  \
0                      0         0       0                 0   
1                      0         0       0                 0   
2                      0         0       0                 0   
3                      0         0       0                 0   
4                      0         0       0                 0   
5                      0         0       0                 0   
6                      0         0       0                 0   
7                      0         0       0                 0   
8                      0         0       0                 0   
9                      0         0       0                 0   
10                     0         0       0                 0   
11                     0         0       0                 0   
12                     0         0       0                 0   
13                     0         0       0                 0   
14                     0         0       0                 0   
15                     0         0       0                 0   
16                     0         0       0                 0   
17                     0         0       0                 0   
18                     0         0       0                 0   
19                     0         0       0                 0   
20                     0         0       0                 0   
21                     0         0       0                 0   
22                     0         0       0                 0   
23                     0         0       0                 0   
24                     0         0       0                 0   
25                     0         0       0                 0   
26                     0         0       0                 0   
27                     0         0       0                 0   
28                     0         0       0                 0   
29                     0         0       0                 0   
30                     0         0       0                 0   
31                     0         0       0                 0   
32                     0         0       0                 0   
33                     0         0       0                 0   
34                     0         0       0                 0   
35                     0         0       0                 0   
36                     0         0       0                 0   
37                     0         0       0                 0   
38                     0         0       0                 0   
39                     0         0       0                 0   
40                     0         0       0                 0   
41                     0         0       0                 0   
42                     0         0       0                 0   
43                     0         0       0                 0   
44                     1         0       0                 0   
45                     0         0       0                 0   
46                     0         0       0                 0   
47                     0         0       0                 0   
48                     0         0       0                 0   
49                     0         0       0                 0   
50                     0         0       0                 0   
51                     0         0       0                 0   
52                     0         0       0                 0   
53                     0         0       0                 0   
54                     0         0       0                 0   
55                     0         0       0                 0   
56                     0         0       0                 0   
57                     0         0       0                 0   
58                     0         0       0                 0   
59                     0         0       0                 0   
60                     0         0       0                 0   
61                     0         0   

In [99]:
miami_onehot['Neighborhood'] = miami_venues['Neighborhood']

fixed_columns = [miami_onehot.columns[-1]] + list(miami_onehot.columns[:-1])
miami_onehot = miami_onehot[fixed_columns]

miami_onehot.head()

Neighborhood  American Restaurant  Aquarium  Arcade  \
0                     Allapattah                    0         0       0   
1                     Allapattah                    0         0       0   
2  Arts & Entertainment District                    0         0       0   
3  Arts & Entertainment District                    0         0       0   
4  Arts & Entertainment District                    0         0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Asian Restaurant  \
0                 0                       0            0                 0   
1                 0                       0            0                 0   
2                 0                       0            0                 0   
3                 0                       0            0                 0   
4                 0                       0            0                 0   

   Athletics & Sports  BBQ Joint  Bakery  Bank  Bar  Beach  Big Box Store  \
0                   0          0       0     0    0      0              0   
1                   0          0       0     0    0      0              0   
2                   0          0       0     0    0      0              0   
3                   0          0       0     0    0      0              0   
4                   0          0       0     0    0      0              0   

   Bistro  Boat or Ferry  Boutique  Brazilian Restaurant  Breakfast Spot  \
0       0              0         0                     0               0   
1       0              0         0                     0               0   
2       0              0         0                     0               0   
3       0              0         0                     0               0   
4       0              0         0                     0               0   

   Brewery  Burger Joint  Café  Camera Store  Caribbean Restaurant  \
0        0             0     0             0                     0   
1        0             0     0             0                     0   
2        0             0     0             0                     0   
3        0             0     0             0                     0   
4        0             0     0             0                     0   

   Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0                   0               0             0            0   
1                   0               0             0            0   
2                   0               0             0            0   
3                   0               0             0            0   
4                   0               0             0            0   

   Comfort Food Restaurant  Concert Hall  Convenience Store  Cosmetics Shop  \
0                        0             0                  0               0   
1                        0             0                  0               0   
2                        0             0                  0               0   
3                        0             0                  0               0   
4                        0             0                  0               0   

   Cuban Restaurant  Cupcake Shop  Department Store  Dessert Shop  Diner  \
0                 0             0                 0             0      0   
1                 0             0                 1             0      0   
2                 0             1                 0             0      0   
3                 0             0                 0             0      0   
4                 0             0                 0             0      0   

   Discount Store  Dive Bar  Dog Run  Donut Shop  Empanada Restaurant  \
0               0         0        0           0                    0   
1               0         0        0           0                    0   
2               0         0        0           0                    0   
3               0         0        0           0                    0   
4               0         0        0           0     

In [100]:
miami_grouped = miami_onehot.groupby('Neighborhood').mean().reset_index()
miami_grouped

Neighborhood  American Restaurant  Aquarium    Arcade  \
0                      Allapattah             0.000000  0.000000  0.000000   
1   Arts & Entertainment District             0.000000  0.000000  0.000000   
2                        Brickell             0.037736  0.000000  0.000000   
3                     Buena Vista             0.034483  0.000000  0.034483   
4                   Coconut Grove             0.333333  0.000000  0.000000   
5                       Coral Way             0.000000  0.000000  0.000000   
6                 Design District             0.035714  0.000000  0.035714   
7                        Downtown             0.040000  0.000000  0.000000   
8                       Edgewater             0.022727  0.000000  0.000000   
9                         Flagami             0.000000  0.000000  0.000000   
10              Grapeland Heights             0.000000  0.000000  0.000000   
11                   Liberty City             0.000000  0.000000  0.000000   
12                   Little Haiti             0.000000  0.000000  0.000000   
13                  Little Havana             0.000000  0.000000  0.000000   
14                    Lummus Park             0.083333  0.000000  0.000000   
15                        Midtown             0.023256  0.000000  0.000000   
16                       Overtown             0.000000  0.000000  0.000000   
17                      Park West             0.038462  0.038462  0.000000   
18                      The Roads             0.000000  0.000000  0.000000   
19                 Upper Eastside             0.000000  0.000000  0.000000   
20               Venetian Islands             0.000000  0.000000  0.000000   
21                   Virginia Key             0.000000  0.000000  0.000000   
22                   West Flagler             0.000000  0.000000  0.000000   
23                        Wynwood             0.026316  0.000000  0.000000   

    Arepa Restaurant  Argentinian Restaurant  Art Gallery  Asian Restaurant  \
0           0.000000                0.000000     0.000000          0.000000   
1           0.000000                0.000000     0.050000          0.000000   
2           0.000000                0.037736     0.000000          0.000000   
3           0.034483                0.000000     0.034483          0.034483   
4           0.000000                0.000000     0.000000          0.000000   
5           0.000000                0.000000     0.000000          0.000000   
6           0.035714                0.000000     0.035714          0.035714   
7           0.000000                0.000000     0.000000          0.000000   
8           0.000000                0.000000     0.045455          0.000000   
9           0.000000                0.000000     0.000000          0.000000   
10          0.000000                0.000000     0.000000          0.000000   
11          0.000000                0.000000     0.000000          0.000000   
12          0.000000                0.041667     0.000000          0.000000   
13          0.000000                0.000000     0.000000          0.000000   
14          0.000000                0.000000     0.000000          0.000000   
15          0.023256                0.023256     0.023256          0.023256   
16          0.000000                0.000000     0.000000          0.000000   
17          0.000000                0.000000     0.038462          0.000000   
18          0.000000                0.000000     0.000000          0.000000   
19          0.000000                0.000000     0.000000          0.000000   
20          0.000000                0.000000     0.000000          0.000000   
21          0.000000                0.000000     0.000000          0.000000   
22          0.000000                0.000000     0.000000          0.000000   
23          0.000000                0.000000     0.157895          0.026316   

    Athletics & Sports  BBQ Joint    Bakery      Bank       Bar  Beach  \
0             0.0000

In [102]:
# Find top 5 types of venues for each neighborhood.
num_top_venues = 5

for hood in miami_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = miami_grouped[miami_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allapattah----
                   venue  freq
0       Department Store   0.5
1                 Lounge   0.5
2  Performing Arts Venue   0.0
3              Nightclub   0.0
4           Nutritionist   0.0


----Arts & Entertainment District----
            venue  freq
0             Gym  0.10
1      Restaurant  0.10
2  Ice Cream Shop  0.10
3     Yoga Studio  0.05
4            Park  0.05


----Brickell----
                 venue  freq
0                Hotel  0.09
1   Italian Restaurant  0.08
2  Japanese Restaurant  0.06
3                 Café  0.06
4  American Restaurant  0.04


----Buena Vista----
                venue  freq
0                Café  0.10
1            Boutique  0.07
2       Jewelry Store  0.07
3  Italian Restaurant  0.07
4         Coffee Shop  0.07


----Coconut Grove----
                     venue  freq
0      American Restaurant  0.33
1                     Park  0.33
2            Boat or Ferry  0.33
3  New American Restaurant  0.00
4                Nightclub  0.00


----

In [103]:
len(miami_grouped[miami_grouped['Italian Restaurant'] > 0])

9

In [104]:
# Creating a new dataframe with Italian Restaurants only.
miami_it = miami_grouped[['Neighborhood', 'Italian Restaurant']]
miami_it.head()

Neighborhood  Italian Restaurant
0                     Allapattah            0.000000
1  Arts & Entertainment District            0.000000
2                       Brickell            0.075472
3                    Buena Vista            0.068966
4                  Coconut Grove            0.000000

## 6. Clustering neighborhoods in Miami.
Using the K-Means Clustering algorithm to cluster neighborhoods in Miami.

In [105]:
# Setting number of clusters and identifying data being used for the clusters. 
k = 3
miami_clustering = miami_it.drop(['Neighborhood'], 1)

# Setting up the K-Means algorithm and feeding it the data.
kmeans = KMeans(n_clusters=k, random_state=0).fit(miami_clustering)
kmeans.labels_[0:10]

array([1, 1, 0, 0, 1, 1, 0, 0, 1, 1], dtype=int32)

In [108]:
# Creating a merged dataframe that includes cluster labels as well as top venues.
miami_merged = miami_it.copy()

# add clustering labels
miami_merged['Cluster Labels'] = kmeans.labels_
miami_merged

Neighborhood  Italian Restaurant  Cluster Labels
0                      Allapattah            0.000000               1
1   Arts & Entertainment District            0.000000               1
2                        Brickell            0.075472               0
3                     Buena Vista            0.068966               0
4                   Coconut Grove            0.000000               1
5                       Coral Way            0.000000               1
6                 Design District            0.071429               0
7                        Downtown            0.060000               0
8                       Edgewater            0.000000               1
9                         Flagami            0.000000               1
10              Grapeland Heights            0.000000               1
11                   Liberty City            0.000000               1
12                   Little Haiti            0.041667               0
13                  Little Havana            0.000000               1
14                    Lummus Park            0.000000               1
15                        Midtown            0.046512               0
16                       Overtown            0.000000               1
17                      Park West            0.000000               1
18                      The Roads            0.111111               2
19                 Upper Eastside            0.166667               2
20               Venetian Islands            0.000000               1
21                   Virginia Key            0.000000               1
22                   West Flagler            0.000000               1
23                        Wynwood            0.013158               1

In [109]:
# Merge venue data along with location data, with cluster data.
miami_merged = miami_merged.join(miami_venues.set_index('Neighborhood'), on='Neighborhood')

miami_merged.head()

Neighborhood  Italian Restaurant  Cluster Labels  \
0                     Allapattah                 0.0               1   
0                     Allapattah                 0.0               1   
1  Arts & Entertainment District                 0.0               1   
1  Arts & Entertainment District                 0.0               1   
1  Arts & Entertainment District                 0.0               1   

   Neighborhood Latitude  Neighborhood Longitude  \
0                 25.815                 -80.224   
0                 25.815                 -80.224   
1                 25.799                 -80.190   
1                 25.799                 -80.190   
1                 25.799                 -80.190   

                            Venue  Venue Latitude  Venue Longitude  \
0   Three Fingers Liquor & Lounge       25.815408       -80.224361   
0                            Ross       25.815820       -80.221753   
1                    Bunnie Cakes       25.799544       -80.190953   
1            Yodi's Threading Spa       25.800490       -80.189093   
1  TRIO - Mind Body Spirit Studio       25.799573       -80.190972   

     Venue Category  
0            Lounge  
0  Department Store  
1      Cupcake Shop  
1               Spa  
1       Yoga Studio

In [110]:
# Sort based on cluster labels.
miami_merged.sort_values(['Cluster Labels'], inplace=True)
miami_merged

Neighborhood  Italian Restaurant  Cluster Labels  \
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
15                        Midtown            0.046512               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
6                 Design District            0.071429               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7                        Downtown            0.060000               0   
7     

In [111]:
# Visualize the clusters.
map_clusters = folium.Map(location=[lat, lng], zoom_start=10)

# Setting the color scheme for the clusters.
x = np.arange(k)
ys = [i+x+(i*x)**2 for i in range(k)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# Add markers to the map.
markers_colors = []
for lat, lon, poi, cluster in zip(miami_merged['Neighborhood Latitude'], miami_merged['Neighborhood Longitude'], miami_merged['Neighborhood'], miami_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 7. Examine the individual clusters.
Dig into the individual clusters to learn more about each one.

In [113]:
# Cluster 0
miami_merged.loc[miami_merged['Cluster Labels'] == 0]

Neighborhood  Italian Restaurant  Cluster Labels  \
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
15          Midtown            0.046512               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
6   Design District            0.071429               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
7          Downtown            0.060000               0   
12     Little Haiti            0.041667               0   
12     Little Haiti            0.041667               0   
12     Little Haiti            0.041667               0   
15          Midtown            0.046512               

In [114]:
# Cluster 1
miami_merged.loc[miami_merged['Cluster Labels'] == 1]

Neighborhood  Italian Restaurant  Cluster Labels  \
17                      Park West            0.000000               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
17                      Park West            0.000000               1   
23                        Wynwood            0.013158               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
16                       Overtown            0.000000               1   
16                       Overtown            0.000000               1   
16                       Overtown            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
23                        Wynwood            0.013158               1   
17                      Park West            0.000000               1   
17                      Park West            0.000000               1   
23                        Wynwood            0.013158               1   
22                   West Flagler            0.000000               1   
17                      Park West            0.000000               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23                        Wynwood            0.013158               1   
23    

In [115]:
# Cluster 2
miami_merged.loc[miami_merged['Cluster Labels'] == 2]

Neighborhood  Italian Restaurant  Cluster Labels  Neighborhood Latitude  \
18       The Roads            0.111111               2                 25.756   
19  Upper Eastside            0.166667               2                 25.830   
19  Upper Eastside            0.166667               2                 25.830   
19  Upper Eastside            0.166667               2                 25.830   
19  Upper Eastside            0.166667               2                 25.830   
19  Upper Eastside            0.166667               2                 25.830   
19  Upper Eastside            0.166667               2                 25.830   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   
18       The Roads            0.111111               2                 25.756   

    Neighborhood Longitude                                       Venue  \
18                 -80.207  Revilla, Antonio Lawyer - Revilla Law Firm   
19                 -80.183                   Morningside Tennis Center   
19                 -80.183                              Shalimar Motel   
19                 -80.183                                  Sushi Siam   
19                 -80.183                   Andiamo! Brick Oven Pizza   
19                 -80.183                                  Cafe Roval   
19                 -80.183                    Europa Car Wash and Cafe   
18                 -80.207                                 Forever Tan   
18                 -80.207                       Yana's Red Devil Car!   
18                 -80.207                        Bocas Grill Brickell   
18                 -80.207                          TUTTO'S MARE MIAMI   
18                 -80.207              Brickell Cosmetic Center & Spa   
18                 -80.207                         Pozo Goldstein, LLP   
18                 -80.207                         JuliENERGYnutrition   
18                 -80.207                                       Shell   

    Venue Latitude  Venue Longitude             Venue Category  
18       25.757580       -80.205546                     Lawyer  
19       25.826468       -80.181455               Tennis Court  
19       25.833877       -80.184497                      Motel  
19       25.827641       -80.187215           Sushi Restaurant  
19       25.827640       -80.186994                Pizza Place  
19       25.829372       -80.187083         Italian Restaurant  
19       25.832404       -80.183642                Gas Station  
18       25.753160       -80.210823    Health & Beauty Service  
18       25.753794       -80.203396              Moving Target  
18       25.755430       -80.207555  Latin American Restaurant  
18       25.755440       -80.207960         Italian Restaurant  
18       25.754582       -80.209865         Salon / Barbershop  
18       25.757904       -80.204386                     Lawyer  
18       25.754670       -80.209950               Nutritionist  
18       25.758927       -80.203544                Gas Station

## Conclusion
The majority of Italian restaurants in cluster 0, which would include neighborhoods such as: Downtown, Midtown, Design District, Little Haiti, Brickell, and Buena Vista. Neighborhoods with few to no Italian restaurants belong to Cluster 1: Park West, Wynwood, Overtown, West Flagler, Virginia Key, Venetian Islands, Allapattah, Edgewater, Lummus Park, Coral Way, Arts & Entertainment District, Coconut Grove, Grapeland Heights, Liberty City, Little Havana, and Flagami. This, however, may be a good place to open an Italian restaurant as there would be few competitors. 